In [4]:
!pip install selenium

In [5]:
import bs4
import requests
import pandas as pd
from selenium import webdriver
from tqdm import tqdm

In [31]:
links = []
i = 18
for k in range(1, 2125):
    links.append(f'http://legacy.senate.gov.ph/lis/'
                 f'bill_res.aspx?congress={i}&q=SBN-{k}')

In [32]:
links[0]

'http://legacy.senate.gov.ph/lis/bill_res.aspx?congress=18&q=SBN-1737'

In [33]:
'http://legacy.senate.gov.ph/lis/bill_res.aspx?congress=18&q=SBN-1737'

'http://legacy.senate.gov.ph/lis/bill_res.aspx?congress=18&q=SBN-1737'

In [8]:
!pip install msedge-selenium-tools

In [34]:
from msedge.selenium_tools import Edge, EdgeOptions

# # Launch Microsoft Edge (Chromium)
# edge_options = EdgeOptions()
# edge_options.use_chromium = True
# edge_options.add_argument('headless')
# # edge_options.add_argument('disable-gpu')

# # Headless
# driver = Edge(options = edge_options)

# With head
driver = webdriver.Edge("C:/Users/nisni/OneDrive/Documents/edgedriver_win64_1/msedgedriver.exe")

In [35]:
result_dict = dict()
for i, url in enumerate(tqdm(links)):
    driver.get(url)
    try:
        button = driver.find_element_by_id('lbAll')
        button.click()
    except:
        continue
    html = driver.page_source
    result_dict[url] = html

100%|████████████████████████████████████████████████████████████████████████████████| 388/388 [05:11<00:00,  1.24it/s]


In [36]:
driver.quit()

In [37]:
pd.to_pickle(result_dict, f"18th_senate_bills.pkl")

In [38]:
result_dict

{'http://legacy.senate.gov.ph/lis/bill_res.aspx?congress=18&q=SBN-1737': '<html xmlns="http://www.w3.org/1999/xhtml"><head><meta http-equiv="Content-Type" content="text/html; charset=utf-8"><title>\n\t18th Congress - Senate Bill No. 1737 - Senate of the Philippines\n</title>\n   <script type="text/javascript" language="javascript" src="/scripts_web/div.js"></script>\n   <link rel="stylesheet" type="text/css" href="/scripts_web/print.css" media="print"><link rel="stylesheet" type="text/css" href="../scripts_web/lis.css" media="all"><link rel="stylesheet" type="text/css" href="../scripts_web/xhtml.css" media="all"><link rel="stylesheet" type="text/css" href="../scripts_web/xhtml_body.css" media="all"></head>\n\n<body>\n   <div class="xhtml_nav"><img alt="Senate of the Philippines banner" src="/images/website_banner18th.jpg" class="nav_logo" width="800" height="96"><div id="nav_top">\n<table><tbody><tr><td><a href="/">Home</a>&nbsp;</td><td>|</td><td><div onmouseover="ShowDiv(\'nav_About\

In [39]:
import pandas as pd
import json
import bs4
import re
from tqdm.notebook import tqdm

In [41]:
with open('bills18.json', 'w') as json_file:
    json.dump(result_dict, json_file)

In [44]:
soup = bs4.BeautifulSoup(list(result_dict.values())[0], 'html.parser')
content = soup.find('td', attrs = {'id':'content'}).text.strip()
content

"18th CongressSenate Bill No. 1737CHARTER OF THE CITY OF CALACAFiled on July 27, 2020 by Gatchalian, Win, Binay, Maria Lourdes Nancy S., Marcos, Imee R.\n            \n\n\n\n\n\n\n//<![CDATA[\nvar theForm = document.forms['form1'];\nif (!theForm) {\n    theForm = document.form1;\n}\nfunction __doPostBack(eventTarget, eventArgument) {\n    if (!theForm.onsubmit || (theForm.onsubmit() != false)) {\n        theForm.__EVENTTARGET.value = eventTarget;\n        theForm.__EVENTARGUMENT.value = eventArgument;\n        theForm.submit();\n    }\n}\n//]]>\n\n\n\n\n\n\n\nOverview\xa0|\n                     Committee Referral\xa0|\n                     \n                     \n                     Leg. History\n|\nAll Information\n\n\n\nDownload SBN-1737 (as filed)8/20/2020 3.4MB\n\n\nLong titleAN ACT CONVERTING THE MUNICIPALITY OF CALACA IN THE PROVINCE OF BATANGAS INTO A COMPONENT CITY TO BE KNOWN AS THE CITY OF CALACA\nScopeLocal\nLegislative statusConsolidated/Substituted in the Committee Repor

In [45]:
values = []

for i in tqdm(list(result_dict.values())):
    dic = {}
    soup = bs4.BeautifulSoup(i, 'html.parser')
    content = soup.find('td', attrs = {'id':'content'}).text.strip()
    try:
        dic['congress'] = int(re.search('\d{2}(?=th Congress)',
                                        content).group(0))
        dic['type'] = re.search('(?<= Congress).+(?= Bill)', content).group(0)
        bill_num = int(re.search('(?<=Bill No. )\d{1,}', content).group(0))
        dic['bill_num'] = bill_num
        dic['title'] = re.search(f'(?<=Bill No. {bill_num}).+(?=Filed)',
                                 content).group(0)
        dic['filed_on'] = re.search('(?<=Filed on ).+(?= by)',
                                    content).group(0)
        dic['filed_by'] = re.search('(?<=by ).+', content).group(0)
        dic['long_title'] = re.search('(?<=Long title).+', content).group(0)
        dic['scope'] = re.search('(?<=Scope).+', content).group(0)
        dic['subjects'] = re.search('(?<=Subject\(s\)).+', content).group(0)
        dic['primary_committee'] = re.search('(?<=Primary committee).+',
                                             content).group(0)
        try:
            dic['secondary_committee'] = re.search('(?<=Secondary committee).+',
                                               content).group(0)
        except:
            pass
        dic['status'] = re.search('(?<=Legislative status).+(?=[,(])',
                            content).group(0).strip()
    except:
        pass
    values.append(dic)

In [46]:
df = pd.DataFrame(values)
df

congress    type  bill_num  \
0          18  Senate      1737   
1          18  Senate      1738   
2          18  Senate      1739   
3          18  Senate      1740   
4          18  Senate      1741   
..        ...     ...       ...   
383        18  Senate      2120   
384        18  Senate      2121   
385        18  Senate      2122   
386        18  Senate      2123   
387        18  Senate      2124   

                                                 title        filed_on  \
0                        CHARTER OF THE CITY OF CALACA   July 27, 2020   
1                             E-GOVERNANCE ACT OF 2020   July 27, 2020   
2                    FINANCIAL CONSUMER PROTECTION ACT   July 27, 2020   
3    RURAL AGRICULTURAL AND FISHERIES FINANCING ENH...   July 27, 2020   
4    CACAO AND CHOCOLATE CAPITAL OF THE PHILIPPINES...   July 27, 2020   
..                                                 ...             ...   
383      ILOCOS SUR PHILIPPINES POLYTECHNIC UNIVERSITY  March 24, 2021   
384                                        RED-TAGGING  March 24, 2021   
385  THE 30-YEAR NATIONAL INFRASTRUCTURE MASTER PLA...  March 24, 2021   
386              EXPANDED STIMULUS PACKAGE ACT OF 2021  March 24, 2021   
387       AMENDING THE SANGGUNIANG KABATAAN REFORM ACT  March 24, 2021   

                                              filed_by  \
0    Gatchalian, Win, Binay, Maria Lourdes Nancy S....   
1                          Go, Christopher Lawrence T.   
2                                           Poe, Grace   
3                                           Poe, Grace   
4    Villar, Cynthia A., Dela Rosa, Ronald "Bato", ...   
..                                                 ...   
383                                    Marcos, Imee R.   
384                                Drilon, Franklin M.   
385                      Pacquiao, Emmanuel "Manny" D.   
386                      Pacquiao, Emmanuel "Manny" D.   
387  Angara, Sonny, Revilla Jr., Ramon Bong, Marcos...   

                                            long_title     scope  \
0    AN ACT CONVERTING THE MUNICIPALITY OF CALACA I...     Local   
1    AN ACT INSTITUTIONALIZING THE TRANSITION OF TH...  National   
2    AN ACT ESTABLISHING A FRAMEWORK FOR THE PROTEC...  National   
3    AN ACT MANDATING BANKING INSTITUTIONS TO STREN...  National   
4    AN ACT DECLARING THE CITY OF DAVAO AS THE CACA...  National   
..                                                 ...       ...   
383  AN ACT CONVERTING THE ILOCOS SUR POLYTECHNIC S...     Local   
384  AN ACT DEFINING AND PENALIZING THE CRIME OF RE...  National   
385  AN ACT ADOPTING A 30-YEAR NATIONAL INFRASTRUCT...  National   
386  AN ACT AUGMENTING THE STIMULUS PACKAGE FOR COV...  National   
387  AN ACT TO FURTHER EMPOWER THE MEMBERS OF THE S...  National   

                                              subjects  \
0                    City Charter, Revision/Amendments   
1    E-Government ServicesDigital TechnologyInforma...   
2     Consumer ProtectionFinancial Consumer Protection   
3    Rural Agricultural and Fisheries Financing Enh...   
4                          Cacao and Chocolate Capital   
..                                                 ...   
383                                Schools, Conversion   
384                            Red-Tagging/Red-Baiting   
385                                    Infrastructures   
386                                           Covid-19   
387                     Sangguniang Kabataan (SK)Youth   

                                primary_committee  \
0                                Local Government   
1                          Science and Technology   
2    Banks, Financial Institutions and Currencies   
3           Agriculture, Food and Agrarian Reform   
4           Agriculture, Food and Agrarian Reform   
..                                            ...   
383    Higher, Technical and Vocational Education   
384                      Justice and Human Rights   
385    

In [48]:
df2 = pd.read_csv('bills.csv')
df2

congress    type  bill_num  \
0            13  Senate         1   
1            13  Senate         2   
2            13  Senate         3   
3            13  Senate         4   
4            13  Senate         5   
...         ...     ...       ...   
15234        18  Senate      1732   
15235        18  Senate      1733   
15236        18  Senate      1734   
15237        18  Senate      1735   
15238        18  Senate      1736   

                                                   title   filed_on  \
0         SPECIAL MEASURES TO LOWER THE COST OF MEDICINE  30-Jun-04   
1                      THE CONSTITUTIONAL CONVENTION ACT  30-Jun-04   
2        MAGNA CARTA OF PATIENT'S RIGHTS AND OBLIGATIONS  30-Jun-04   
3                           HEALTH PROMOTION ACT OF 2004  30-Jun-04   
4      INCREASING THE ALLOWABLE PERSONAL ADDITIONAL T...  30-Jun-04   
...                                                  ...        ...   
15234  CONVERTING THE ARAKAN-CALINAN MUNICIPAL ROAD I...  23-Jul-20   
15235                                 UNIVERSITY OF ABRA  23-Jul-20   
15236  CAGAYAN VALLEY MEDICAL CENTER – ABULUG EXTENSI...  23-Jul-20   
15237                        BINENG NATIONAL HIGH SCHOOL  23-Jul-20   
15238  CONVERTING THE MONGGAYANG, MUNICIPALITY OF AGU...  27-Jul-20   

                                   filed_by  \
0      Flavier, Juan M., Angara, Edgardo J.   
1                          Flavier, Juan M.   
2      Flavier, Juan M., Angara, Edgardo J.   
3      Flavier, Juan M., Angara, Edgardo J.   
4                          Flavier, Juan M.   
...                                     ...   
15234                       Marcos, Imee R.   
15235                       Marcos, Imee R.   
15236                       Marcos, Imee R.   
15237                       Marcos, Imee R.   
15238                       Marcos, Imee R.   

                                              long_title     scope  \
0      AN ACT PRESCRIBING SPECIAL  MEASURES  TO LOWER...  National   
1      AN ACT CALLING FOR A  CONSTITUTIONAL CONVENTIO...  National   
2      AN ACT DECLARING THE RIGHTS  AND OBLIGATIONS O...  National   
3      AN ACT ESTABLISHING A  NATIONAL HEALTH PROMOTI...  National   
4      AN ACT INCREASING THE ALLOWABLE PERSONAL ADDIT...  National   
...                                                  ...       ...   
15234  AN ACT CONVERTING THE ARAKAN-CALINAN MUNICIPAL...     Local   
15235  AN ACT CONVERTING THE ABRA STATE INSTITUTE OF ...     Local   
15236  AN ACT ESTABLISHING A THIRTY (30) – BED DISTRI...     Local   
15237  AN ACT CONVERTING THE BENGUET NATIONAL HIGH SC...     Local   
15238  AN ACT CONVERTING THE MONGGAYANG, MUNICIPALITY...     Local   

                                                subjects  \
0      Medicines (Lowering the Cost)           Drugs/...   
1      Constitutional Convention               Charte...   
2      Patients Rights and Obligations         Magna ...   
3      National Health Promotion Institute     Philip...   
4      Taxes (Tax Exemption-Individual TaxpayerNation...   
...                                                  ...   
15234                                  Roads, Conversion   
15235                                Schools, Conversion   
15236                           Hospitals, Establishment   
15237                                Schools, Conversion   
15238                                  Roads, Conversion   

                                       primary_committee  \
0                                  Health and Demography   
1      Constitutional Amendments, Revision of Codes a...   
2                                  Health and Demography   
3         Government Corporations and Public Enterprises   
4                                         Ways and Means   
...                                                  ...   
15234                                              Rules   
15235         Higher, Technical and Vocational Education   
15236                                     

In [52]:
df3 = df2.append(df).reset_index(drop=True)

In [54]:
df3.to_csv('NS_senators.csv', index=False)